In [1]:
%matplotlib inline
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from sklearn import linear_model
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA 
from sklearn import ensemble
from sklearn.model_selection import cross_val_score
from sklearn.feature_selection import RFE
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier

df = pd.read_csv("ks-projects-201801.csv", encoding='latin1', low_memory=False)

df_test = df.drop(df.index[[1, 50000]])

df_validate = df.sample(50000)

df_validate.head()

df_test.head()

ID                                               name  \
0  1000002330                    The Songs of Adelaide & Abullah   
2  1000004038                                     Where is Hank?   
3  1000007540  ToshiCapital Rekordz Needs Help to Complete Album   
4  1000011046  Community Film Project: The Art of Neighborhoo...   
5  1000014025                               Monarch Espresso Bar   

         category main_category currency    deadline     goal  \
0          Poetry    Publishing      GBP  2015-10-09   1000.0   
2  Narrative Film  Film & Video      USD  2013-02-26  45000.0   
3           Music         Music      USD  2012-04-16   5000.0   
4    Film & Video  Film & Video      USD  2015-08-29  19500.0   
5     Restaurants          Food      USD  2016-04-01  50000.0   

              launched  pledged       state  backers country  usd pledged  \
0  2015-08-11 12:12:28      0.0      failed        0      GB          0.0   
2  2013-01-12 00:20:50    220.0      failed        3      US        220.0   
3  2012-03-17 03:24:11      1.0      failed        1      US          1.0   
4  2015-07-04 08:35:03   1283.0    canceled       14      US       1283.0   
5  2016-02-26 13:38:27  52375.0  successful      224      US      52375.0   

   usd_pledged_real  usd_goal_real  
0               0.0        1533.95  
2             220.0       45000.00  
3               1.0        5000.00  
4            1283.0       19500.00  
5           52375.0       50000.00

In [3]:
df_test.isnull().sum()

df_test.dropna(inplace=True)

df_test.isnull().sum()

ID                  0
name                0
category            0
main_category       0
currency            0
deadline            0
goal                0
launched            0
pledged             0
state               0
backers             0
country             0
usd pledged         0
usd_pledged_real    0
usd_goal_real       0
dtype: int64

In [15]:
df2=df_test[['category', 'usd_goal_real', 'country', 'usd_pledged_real',]]

df2_dummies = pd.get_dummies(df2, prefix_sep="_", drop_first=True)

df2.head()

df2_dummies.head()

usd_goal_real  usd_pledged_real  category_Academic  category_Accessories  \
0        1533.95               0.0                  0                     0   
2       45000.00             220.0                  0                     0   
3        5000.00               1.0                  0                     0   
4       19500.00            1283.0                  0                     0   
5       50000.00           52375.0                  0                     0   

   category_Action  category_Animals  category_Animation  \
0                0                 0                   0   
2                0                 0                   0   
3                0                 0                   0   
4                0                 0                   0   
5                0                 0                   0   

   category_Anthologies  category_Apparel  category_Apps     ...      \
0                     0                 0              0     ...       
2                     0                 0              0     ...       
3                     0                 0              0     ...       
4                     0                 0              0     ...       
5                     0                 0              0     ...       

   country_IT  country_JP  country_LU  country_MX  country_NL  country_NO  \
0           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   
5           0           0           0           0           0           0   

   country_NZ  country_SE  country_SG  country_US  
0           0           0           0           0  
2           0           0           0           1  
3           0           0           0           1  
4           0           0           0           1  
5           0           0           0           1  

[5 rows x 181 columns]

In [16]:
#i dont know what these values mean
from sklearn import preprocessing
from sklearn import utils

y_bins = [-1, 49999, 99999, 499999, 999999, 24999999]

y_bins_labels = ["0-50,000", "50,000-100,000", "100,000-500,000", "500,000-1,000,000", "1,000,000+"]

df2_dummies["USD_Pledged_Bins"] = pd.cut(df2_dummies["usd_pledged_real"], y_bins, labels=y_bins_labels)

df2_dummies.head()

# lab_enc = preprocessing.LabelEncoder()
# encoded = lab_enc.fit_transform(y)

# print(utils.multiclass.type_of_target(encoded))

usd_goal_real  usd_pledged_real  category_Academic  category_Accessories  \
0        1533.95               0.0                  0                     0   
2       45000.00             220.0                  0                     0   
3        5000.00               1.0                  0                     0   
4       19500.00            1283.0                  0                     0   
5       50000.00           52375.0                  0                     0   

   category_Action  category_Animals  category_Animation  \
0                0                 0                   0   
2                0                 0                   0   
3                0                 0                   0   
4                0                 0                   0   
5                0                 0                   0   

   category_Anthologies  category_Apparel  category_Apps        ...         \
0                     0                 0              0        ...          
2                     0                 0              0        ...          
3                     0                 0              0        ...          
4                     0                 0              0        ...          
5                     0                 0              0        ...          

   country_JP  country_LU  country_MX  country_NL  country_NO  country_NZ  \
0           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   
5           0           0           0           0           0           0   

   country_SE  country_SG  country_US  USD_Pledged_Bins  
0           0           0           0          0-50,000  
2           0           0           1          0-50,000  
3           0           0           1          0-50,000  
4           0           0           1          0-50,000  
5           0           0           1    50,000-100,000  

[5 rows x 182 columns]

In [5]:
# from sklearn.preprocessing import LabelEncoder

# X = df2["category"]

# # Step 1: Label-encode data set
# label_encoder = LabelEncoder()
# label_encoder.fit(X)
# encoded_X = label_encoder.transform(X)

In [6]:
# encoded_X

In [7]:
# for label, original_class in zip(encoded_X, X):
#     print('Original Class: ' + str(original_class))
#     print('Encoded Label: ' + str(label))
#     print('-' * 12)

In [ ]:
# from keras.utils import to_categorical

# # Step 2: One-hot encoding
# one_hot_X = to_categorical(encoded_X)
# one_hot_X

In [ ]:
# df2.head()

In [ ]:
# #I need to fix this so to that one hot encoding don't know how to yet
# df2['categories']=np.where(df2.category=='Product Design',1,
#     np.where(df2.category=='Tabletop Games',2,
#              np.where(df2.category=='Video Games',3,
#                       np.where(df2.category=='Hardware',4,
#                                np.where(df2.category=='Documentary',5,
#                                         np.where(df2.category=='Technology',6,
#                                                  np.where(df2.category=='Food',7,
#                                                           np.where(df2.category=='Gadgets',8,
#                                                                    np.where(df2.category=='Music',9,
#                                                                             np.where(df2.category=='Narrative Film',10,0))))))))))

In [6]:
# df2 = df2[df2['categories'] != 0]
# df2.head()

category      goal  pledged  categories
1  Narrative Film   30000.0   2421.0          10
2  Narrative Film   45000.0    220.0          10
3           Music    5000.0      1.0           9
6            Food    1000.0   1205.0           7
8  Product Design  125000.0   8233.0           1

In [11]:
# from sklearn.preprocessing import LabelEncoder

# # Step 1: Label-encode data set
# label_encoder = LabelEncoder()
# label_encoder.fit(X)
# encoded_X = label_encoder.transform(X)

In [12]:
# for label, original_class in zip(encoded_X, X):
#     print('Original Class: ' + str(original_class))
#     print('Encoded Label: ' + str(label))
#     print('-' * 12)

Original Class: 10
Encoded Label: 9
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 2
Encoded Label: 1
-

Encoded Label: 0
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 8
Encoded Label: 7
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 3
Encoded Label: 2
------------
Original

------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 4
Encoded Label: 3
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 8
Encoded Label: 7
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 6
Encoded

Encoded Label: 4
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 4
Encoded Label: 3
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 9
Encoded Label: 8
------------
Original

------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 9
Encoded L

...

Encoded Label: 3
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 7
Encoded Label: 6
------------
Original 

------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 4
Encoded Label: 3
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 5
Encoded L

Original Class: 9
Encoded Label: 8
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 8
Encoded Label: 7
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 2
Encoded Label: 1
-----

Original Class: 9
Encoded Label: 8
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 8
Encoded Label: 7
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 8
Encoded Label: 7
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 4
Encoded Label: 3
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 7
Encoded Label: 6
------------
Original Class: 4
Encoded Label: 3
-----

Encoded Label: 6
------------
Original Class: 6
Encoded Label: 5
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 10
Encoded Label: 9
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 5
Encoded Label: 4
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 4
Encoded Label: 3
------------
Original Class: 1
Encoded Label: 0
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 2
Encoded Label: 1
------------
Original Class: 9
Encoded Label: 8
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 3
Encoded Label: 2
------------
Original Class: 3
Encoded Label: 2
------------
Original 

In [13]:
# from keras.utils import to_categorical

# # Step 2: One-hot encoding
# one_hot_X = to_categorical(encoded_X)
# one_hot_X

/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


array([[0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 1., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [17]:
X = df2_dummies.drop(columns=["usd_pledged_real","USD_Pledged_Bins"])
y = df2_dummies["USD_Pledged_Bins"]

In [18]:
X.head()

usd_goal_real  category_Academic  category_Accessories  category_Action  \
0        1533.95                  0                     0                0   
2       45000.00                  0                     0                0   
3        5000.00                  0                     0                0   
4       19500.00                  0                     0                0   
5       50000.00                  0                     0                0   

   category_Animals  category_Animation  category_Anthologies  \
0                 0                   0                     0   
2                 0                   0                     0   
3                 0                   0                     0   
4                 0                   0                     0   
5                 0                   0                     0   

   category_Apparel  category_Apps  category_Architecture     ...      \
0                 0              0                      0     ...       
2                 0              0                      0     ...       
3                 0              0                      0     ...       
4                 0              0                      0     ...       
5                 0              0                      0     ...       

   country_IT  country_JP  country_LU  country_MX  country_NL  country_NO  \
0           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   
5           0           0           0           0           0           0   

   country_NZ  country_SE  country_SG  country_US  
0           0           0           0           0  
2           0           0           0           1  
3           0           0           0           1  
4           0           0           0           1  
5           0           0           0           1  

[5 rows x 180 columns]

In [19]:
y.head()

0          0-50,000
2          0-50,000
3          0-50,000
4          0-50,000
5    50,000-100,000
Name: USD_Pledged_Bins, dtype: category
Categories (5, object): [0-50,000 < 50,000-100,000 < 100,000-500,000 < 500,000-1,000,000 < 1,000,000+]

In [20]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=0, stratify=y)

In [21]:
X_test.head()

usd_goal_real  category_Academic  category_Accessories  \
54745        15000.00                  0                     0   
377897       15000.00                  0                     0   
86577        27578.60                  0                     0   
135788         400.00                  0                     0   
312821        1908.71                  0                     0   

        category_Action  category_Animals  category_Animation  \
54745                 0                 0                   0   
377897                0                 0                   0   
86577                 0                 0                   0   
135788                0                 0                   0   
312821                0                 0                   0   

        category_Anthologies  category_Apparel  category_Apps  \
54745                      0                 0              0   
377897                     0                 0              0   
86577                      0                 0              0   
135788                     0                 0              0   
312821                     0                 0              0   

        category_Architecture     ...      country_IT  country_JP  country_LU  \
54745                       0     ...               0           0           0   
377897                      0     ...               0           0           0   
86577                       0     ...               0           0           0   
135788                      0     ...               0           0           0   
312821                      0     ...               0           0           0   

        country_MX  country_NL  country_NO  country_NZ  country_SE  \
54745            0           0           0           0           0   
377897           0           0           0           0           0   
86577            0           0           0           0           0   
135788           0           0           0           0           0   
312821           0           0           0           0           0   

        country_SG  country_US  
54745            0           1  
377897           0           1  
86577            0           0  
135788           0           1  
312821           0           0  

[5 rows x 180 columns]

In [24]:
rfc = ensemble.RandomForestClassifier(n_jobs=-1, n_estimators=500)

rfc.fit(X_train, y_train)

print('train score:', rfc.score(X_train, y_train))
print('test score:', rfc.score(X_test, y_test))


train score: 0.9787794823274988
test score: 0.9667395827775703


In [23]:
# Declare a logistic regression classifier.
# Parameter regularization coefficient C described above.
lr = LogisticRegression(penalty='l2', solver='liblinear')

# Fit the model.
fit = lr.fit(X_train, y_train)

# Display.
# print('Coefficients')
# print(fit.coef_)
# print(fit.intercept_)

pred_y_sklearn_train = lr.predict(X_train)
pred_y_sklearn_test = lr.predict(X_test)

print('\n Accuracy by success (train)')
print(pd.crosstab(pred_y_sklearn_train, y_train))

print('\n Percentage accuracy (train)')
print(lr.score(X_train, y_train))

print('\n Accuracy by success (test)')
print(pd.crosstab(pred_y_sklearn_test, y_test))

print('\n Percentage accuracy (test)')
print(lr.score(X_test, y_test))

# CV
# scores = cross_val_score(lr, X, y, cv=10)

# print(scores)



 Accuracy by success
USD_Pledged_Bins  0-50,000  50,000-100,000  100,000-500,000  \
row_0                                                         
0-50,000            273203            4228             3175   

USD_Pledged_Bins  500,000-1,000,000  1,000,000+  
row_0                                            
0-50,000                        331         206  

 Percentage accuracy
0.9717581444318372

 Accuracy by success
USD_Pledged_Bins  0-50,000  50,000-100,000  100,000-500,000  \
row_0                                                         
0-50,000             91068            1409             1059   

USD_Pledged_Bins  500,000-1,000,000  1,000,000+  
row_0                                            
0-50,000                        110          69  

 Percentage accuracy
0.9717547884543563
